In [1]:
import sqlite3 as sql
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import random
import yaml
import subprocess
import os

import runMops
import MopsAnalysis
import MopsReader
import MopsPlotter
from MopsTracker import MopsTracker
from MopsParameters import MopsParameters
from MopsResults import MopsResults

% matplotlib inline

In [2]:
dataDrive = "/Volumes/DataCenter/"
dataLocation = "neosimData/jpl/oc28-30EditedSSMIDs.txt"
subsampleLocation = "neosimData/jpl_2016_04_20_chiProb00_maxRMS005_trackAdd05_detErr4000_accel50/"
runLocation = dataDrive + subsampleLocation

In [3]:
dets_df = MopsReader.readDetectionsIntoDataframe(dataDrive + dataLocation)
dets_df

visitId  objectId          ra        dec           mjd      mag  \
diaId                                                                    
0      1632978         0  176.493376 -11.783686  52390.965381  20.1233   
1      1632981         1  173.720592  -4.184379  52390.967172  20.0718   
2      1632982         2  174.183623  -2.062412  52390.967618  18.0567   
3      1632982         3  174.496816  -3.012748  52390.967618  20.0325   
4      1632982         1  173.721745  -4.183480  52390.967618  20.0708   
5      1632983         4  168.551646 -14.376801  52390.969452  19.6707   
6      1632988         1  173.733460  -4.174343  52390.972152  20.0851   
7      1632991         5  180.172511 -14.736185  52390.973526  18.8048   
8      1632996         6  184.203462 -24.600833  52390.976214  21.2715   
9      1632996         7  183.562673 -25.323302  52390.976214  15.4981   
10     1633003         5  180.215262 -14.725188  52390.979534  18.8211   
11     1633004         8  183.990336 -11.110103  52390.979982  19.8211   
12     1633007         9  179.068281  -5.609177  52390.981327  18.4735   
13     1633008        10  175.609316  -1.876057  52390.981774  17.0232   
14     1633009        10  175.608885  -1.876353  52390.982221  17.0216   
15     1633011        11  171.094242   3.775007  52390.983115  21.2975   
16     1633012         2  174.181114  -2.060461  52390.983593  18.0582   
17     1633012         3  174.511390  -3.013330  52390.983593  20.0494   
18     1633012         1  173.762962  -4.151301  52390.983593  20.1092   
19     1633012        12  171.690247  -2.289336  52390.983593  20.4214   
20     1633019        13  179.055780  -0.775773  52390.986740  20.0554   
21     1633020        10  175.604093  -1.879639  52390.987188  17.0290   
22     1633023        10  175.602177  -1.880952  52390.989173  17.0342   
23     1633025        13  179.056819  -0.774189  52390.990068  20.0572   
24     1633026        14  178.596763   2.730313  52390.990515  18.4180   
25     1633027        15  177.925368  -4.636467  52390.991002  18.6802   
26     1633030         8  183.990924 -11.106341  52390.992348  19.8220   
27     1633031         8  183.990945 -11.106205  52390.992796  19.8237   
28     1633032        16  180.332142 -12.903622  52390.993244  21.4741   
29     1633034         0  176.487141 -11.776941  52390.994146  20.1296   
...        ...       ...         ...        ...           ...      ...   
85916  1685037      4621    4.456025  -3.145341  52480.365985  20.5515   
85917  1685051      4053  344.504455  -5.943825  52480.372351  21.6314   
85918  1685051      2673  344.474309  -4.739587  52480.372351  19.1544   
85919  1685055      4127  354.041522 -20.439196  52480.374172  21.6128   
85920  1685056      2162  354.723231 -22.352228  52480.374636  21.3456   
85921  1685061       400  355.933506 -30.070434  52480.376926  20.6530   
85922  1685063      2179  350.143662 -27.955979  52480.377824  21.2843   
85923  1685065       400  355.932938 -30.070635  52480.378773  20.6528   
85924  1685078      7515  351.518776 -41.213878  52480.384698  21.8851   
85925  1685081       212    0.525186 -38.673380  52480.386073  18.7376   
85926  1685084       401    8.945181 -34.807313  52480.387550  21.4049   
85927  1685087      1794    9.075592 -47.994437  52480.389103  19.7589   
85928  1685094       466   25.042086 -48.293492  52480.392286  21.3330   
85929  1685100      6540   31.699331 -56.624866  52480.394975  21.7958   
85930  1685102      5350  345.916119 -11.300958  52480.396867  21.6559   
85931  1685105      3523  350.076498 -14.888349  52480.398241  21.4149   
85932  1685106      4127  354.041095 -20.444591  52480.398715  21.6113   
85933  1685107      2162  354.736785 -22.349043  52480.399172  21.3424   
85934  1685111       400  355.926102 -30.073044  52480.400991  20.6517   
85935  1685114      2179  350.154804 -27.946381  52480.402347  21.2803   
85936  1685116       400  355.925400 -30.073291  52480.403276  20.6513   
85937  1685

In [4]:
MopsPlotter.plotDataframe(dets_df)

In [5]:
nightly = dataDrive + "neosimData/jpl/nightly/"

! rm -rf {nightly}
! mkdir {nightly}

In [6]:
call = ["python", os.getenv("MOPS_DIR") + "/bin/splitByNight.py", "-n", nightly, dataDrive + dataLocation]
subprocess.call(call);

In [7]:
parameters = MopsParameters(velocity_max="10.0", ra_acceleration_max="5.0", dec_acceleration_max="5.0", detection_error_threshold="0.4")
tracker = MopsTracker(runLocation)
tracker.getDetections(nightly)

------- MOPS Parameters --------
Current Parameter Values:

---- findTracklets ----
	Maximum velocity:                         10.0
	Minimum velocity:                         0.0
---- collapseTracklets ----
	Right Ascension tolerance:                0.002
	Declination tolerance:                    0.002
	Angular tolerance:                        5
	Velocity tolerance:                       0.05
	Method:                                   greedy
	Use RMS filter:                           True
	Maximum RMS:                              0.001
---- purifyTracklets ----
	Maximum RMS:                              0.001
---- removeSubsets (tracklets) ----
	Remove subsets:                           False
	Keep only longest:                        False
---- makeLinkTrackletsInput_byNight.py ----
	Window size:                              15
---- linkTracklets ----
	Detection error threshold:                0.4
	Maximum right ascension acceleration:     5.0
	Maximum declination acceleration:    

In [8]:
parameters, tracker = runMops.runMops(parameters, tracker, overwrite=True)

------- Run MOPS -------
Running LSST's Moving Object Pipeline

Overwrite triggered: clearing tracker...

Found 72 detection files in /Volumes/DataCenter/neosimData/jpl/nightly/.

Saving parameters to /Volumes/DataCenter/neosimData/jpl_2016_04_20_chiProb00_maxRMS005_trackAdd05_detErr4000_accel50/parameters.yaml

------- Run MOPS -------
Running findTracklets...
Completed running findTracklets.

Saving tracker to /Volumes/DataCenter/neosimData/jpl_2016_04_20_chiProb00_maxRMS005_trackAdd05_detErr4000_accel50/tracker.yaml

------- Run MOPS -------
Running idsToIndices.py...
Completed running idsToIndices.py.

Saving tracker to /Volumes/DataCenter/neosimData/jpl_2016_04_20_chiProb00_maxRMS005_trackAdd05_detErr4000_accel50/tracker.yaml

------- Run MOPS -------
Running collapseTracklets...
Completed running collapseTracklets.

------- Run MOPS -------
Running indicesToIds.py...
Completed running indicesToIds.py.

Saving tracker to /Volumes/DataCenter/neosimData/jpl_2016_04_20_chiProb00_maxR

In [3]:
parameters = MopsParameters.fromYaml(runLocation + "parameters.yaml")
tracker = MopsTracker.fromYaml(runLocation + "tracker.yaml")

Loading parameters from /Volumes/DataCenter/neosimData/jpl_2016_04_20_chiProb00_maxRMS005_trackAdd05_detErr4000_accel50/parameters.yaml
Loading tracker from /Volumes/DataCenter/neosimData/jpl_2016_04_20_chiProb00_maxRMS005_trackAdd05_detErr4000_accel50/tracker.yaml


In [ ]:
results, df = MopsAnalysis.analyze(parameters, tracker, fullDetFile=dataDrive + dataLocation, overwrite=True)

 Overwrite triggered: deleting existing results directory...

Initializing new results object...
Creating DiaSources table...
Creating AllObjects table...
Creating FoundObjects view...
Creating MissedObjects view...
Creating AllTracklets table...
Creating TrackletMembers table...
Creating Tracklets view...
Creating CollapsedTracklets view...
Creating PurifiedTracklets view...
Creating FinalTracklets view...

Reading full detections file into dataframe...
Counting findable objects as tracklets...
Counting findable objects as tracks...
Building objects dataframe...
Updating objects dataframe...
Reading full detections file into database...

Starting tracklet analysis for 72 nights...

Starting tracklet analysis for night 52391 at Thu May  5 22:24:02 2016

- Writing results to /Volumes/DataCenter/neosimData/jpl_2016_04_20_chiProb00_maxRMS005_trackAdd05_detErr4000_accel50/results/52391.results
- Checking file sizes...
- Reading input detections...
- Counting findable objects...
- Updating 

In [ ]:
results = MopsResults.fromYaml(runLocation + "results.yaml")

In [ ]:
import MopsDatabase
import MopsPlotter

In [ ]:
con = sql.connect(tracker.mainDatabase)
window_dbs = MopsDatabase.attachDatabases(con, tracker.windowDatabases)

In [ ]:
results.performanceRatio

In [ ]:
MopsPlotter.plotHists(con)

In [ ]:
completion = MopsDatabase.findFoundObjects(con)["objectId"].nunique() /  float(MopsDatabase.findFindableObjects(con)["objectId"].nunique())

In [ ]:
completion